In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Hypertension"
cohort = "GSE117261"

# Input paths
in_trait_dir = "../../input/GEO/Hypertension"
in_cohort_dir = "../../input/GEO/Hypertension/GSE117261"

# Output paths
out_data_file = "../../output/preprocess/Hypertension/GSE117261.csv"
out_gene_data_file = "../../output/preprocess/Hypertension/gene_data/GSE117261.csv"
out_clinical_data_file = "../../output/preprocess/Hypertension/clinical_data/GSE117261.csv"
json_path = "../../output/preprocess/Hypertension/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Systems Analysis of the Human Pulmonary Arterial Hypertension Lung Transcriptome"
!Series_summary	"Rationale:"
!Series_summary	"Pulmonary arterial hypertension (PAH) is characterized by increased pulmonary artery pressure and vascular resistance, typically leading to right heart failure and death. Current therapies improve quality of life of the patients but have a modest effect on long-term survival. A detailed transcriptomics and systems biology view of the PAH lung is expected to provide new testable hypotheses for exploring novel treatments."
!Series_summary	""
!Series_summary	"Objectives:"
!Series_summary	"Complete transcriptomics analysis of PAH and control lung tissue to develop disease-specific and clinical data/tissue pathology gene expression classifiers from expression datasets. Gene expression data were integrated into pathway analyses."
!Series_summary	""
!Series_summary	"Methods:"
!Series_summary	"Gene expression microarray data was 

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
# 1. Gene Expression Data Availability
# Based on background information, this is a gene expression microarray study on PAH,
# so it should contain gene expression data
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability
# For trait (Hypertension/PAH):
# Looking at the sample characteristics dictionary, key 1 contains 'clinical_group' which indicates PAH status
# Key 2 contains 'pah_subtype' which further categorizes PAH patients
trait_row = 1  # Using clinical_group

# For age:
# Age information is not available in the sample characteristics dictionary
age_row = None

# For gender:
# Key 3 contains 'Sex' information (Male/Female)
gender_row = 3

# 2.2 Data Type Conversion
def convert_trait(value):
    """Convert trait value to binary (0: control, 1: case)"""
    if value is None:
        return None
    
    # Extract value after colon if present
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # PAH = 1, control (Failed Donor/FD) = 0
    if value == 'all PAH':
        return 1
    elif value == 'FD':  # FD = Failed Donor (control)
        return 0
    else:
        return None

def convert_age(value):
    """Convert age value to continuous"""
    # Age data is not available
    return None

def convert_gender(value):
    """Convert gender value to binary (0: female, 1: male)"""
    if value is None:
        return None
    
    # Extract value after colon if present
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    if value.lower() == 'female':
        return 0
    elif value.lower() == 'male':
        return 1
    else:
        return None

# 3. Save Metadata
# Trait data is available (trait_row is not None)
is_trait_available = trait_row is not None
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
# Only execute if trait_row is not None
if trait_row is not None:
    # Create a DataFrame from the sample characteristics dictionary
    sample_chars = {0: ['tissue: Lung'], 
                    1: ['clinical_group: all PAH', 'clinical_group: FD'], 
                    2: ['pah_subtype: IPAH', 'pah_subtype: APAH', 'pah_subtype: WHO 4', 
                        'pah_subtype: Failed Donor', 'pah_subtype: FPAH', 'pah_subtype: Other'], 
                    3: ['Sex: Female', 'Sex: Male']}
    
    # Convert the dictionary to a format suitable for geo_select_clinical_features
    # The function expects a DataFrame where each column is a sample
    # We'll create a sample column for each unique value combination
    
    # First, create all combinations of values from each row
    all_values = []
    for row_idx in sorted(sample_chars.keys()):
        values = []
        for item in sample_chars[row_idx]:
            values.append(item)
        all_values.append(values)
    
    # Create a DataFrame with these values
    clinical_data = pd.DataFrame({i: [all_values[j][0] for j in range(len(all_values))] 
                                for i in range(1)})
    
    # Extract clinical features
    selected_clinical_df = geo_select_clinical_features(
        clinical_df=clinical_data,
        trait=trait,
        trait_row=trait_row,
        convert_trait=convert_trait,
        age_row=age_row,
        convert_age=convert_age,
        gender_row=gender_row,
        convert_gender=convert_gender
    )
    
    # Preview the extracted features
    preview = preview_df(selected_clinical_df)
    print("Preview of clinical data:")
    print(preview)
    
    # Save the clinical data
    os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
    selected_clinical_df.to_csv(out_clinical_data_file)


Preview of clinical data:
{0: [1.0, 0.0]}


### Step 3: Gene Data Extraction

In [4]:
# 1. First get the file paths again to access the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Use the get_genetic_data function from the library to get the gene_data from the matrix_file
gene_data = get_genetic_data(matrix_file)

# 3. Print the first 20 row IDs (gene or probe identifiers) for future observation
print("First 20 gene/probe identifiers:")
print(gene_data.index[:20])


First 20 gene/probe identifiers:
Index(['7892501', '7892502', '7892503', '7892504', '7892505', '7892506',
       '7892507', '7892508', '7892509', '7892510', '7892511', '7892512',
       '7892513', '7892514', '7892515', '7892516', '7892517', '7892518',
       '7892519', '7892520'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# The gene identifiers shown are probe IDs from an Illumina microarray
# These appear to be Illumina HumanRef-8 v3.0 BeadChip probe IDs
# They are not human gene symbols but numeric identifiers 
# These would need to be mapped to official gene symbols for analysis

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['7896736', '7896738', '7896740', '7896742', '7896744'], 'GB_LIST': [nan, nan, 'NM_001004195,NM_001005240,NM_001005484,BC136848,BC136867,BC136907,BC136908', 'NR_024437,XM_006711854,XM_006726377,XR_430662,AK298283,AL137655,BC032332,BC118988,BC122537,BC131690,NM_207366,AK301928,BC071667', 'NM_001005221,NM_001005224,NM_001005277,NM_001005504,BC137547,BC137568'], 'SPOT_ID': ['chr1:53049-54936', 'chr1:63015-63887', 'chr1:69091-70008', 'chr1:334129-334296', 'chr1:367659-368597'], 'seqname': ['chr1', 'chr1', 'chr1', 'chr1', 'chr1'], 'RANGE_GB': ['NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10'], 'RANGE_STRAND': ['+', '+', '+', '+', '+'], 'RANGE_START': ['53049', '63015', '69091', '334129', '367659'], 'RANGE_STOP': ['54936', '63887', '70008', '334296', '368597'], 'total_probes': [7.0, 31.0, 24.0, 6.0, 36.0], 'gene_assignment': ['---', 'ENST00000328113 // OR4G2P // olfactory receptor, family 4, subfamily G, member 2 pseudogene // ---

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Determine which columns in the gene annotation dataframe contain our identifiers and gene symbols
# Looking at the annotation data, 'ID' contains the probe IDs which match our gene expression data
# The 'gene_assignment' column contains information about gene symbols

# 2. Create a gene mapping dataframe using get_gene_mapping from the library
gene_mapping = get_gene_mapping(gene_annotation, 'ID', 'gene_assignment')

# 3. Apply the gene mapping to convert probe-level measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Normalize gene symbols to official gene symbols using the library function
gene_data = normalize_gene_symbols_in_index(gene_data)

# Preview the processed gene data
print("Preview of gene expression data (after mapping to gene symbols):")
print(gene_data.shape)
print("First few gene symbols:")
print(gene_data.index[:10])


Preview of gene expression data (after mapping to gene symbols):
(24229, 83)
First few gene symbols:
Index(['A1BG', 'A1CF', 'A2M', 'A2ML1', 'A3GALT2', 'A4GALT', 'A4GNT', 'AAA1',
       'AAAS', 'AACS'],
      dtype='object', name='Gene')


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize gene symbols in the gene expression data (already done in step 6)
# Save the normalized gene data to file
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# 2. Extract clinical features from the original clinical data
selected_clinical_df = geo_select_clinical_features(
    clinical_df=clinical_data,
    trait=trait,
    trait_row=trait_row,
    convert_trait=convert_trait,
    age_row=age_row,
    convert_age=convert_age,
    gender_row=gender_row,
    convert_gender=convert_gender
)

# Save the extracted clinical features to a CSV file
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
selected_clinical_df.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# 3. Link the clinical and genetic data
linked_data = geo_link_clinical_genetic_data(selected_clinical_df, gene_data)
print(f"Shape of linked data before missing value handling: {linked_data.shape}")

# 4. Handle missing values systematically
linked_data = handle_missing_values(linked_data, trait)
print(f"Shape of linked data after missing value handling: {linked_data.shape}")

# 5. Check if the dataset is still viable (has enough data)
if linked_data.shape[0] <= 1 or linked_data.shape[1] <= 4:  # No samples or just metadata columns
    is_biased = True
    note = "Dataset failed preprocessing: Insufficient data remained after missing value handling."
    print("Warning: Insufficient data remains after missing value handling!")
else:
    # Check if the trait and demographic features are severely biased
    is_biased, linked_data = judge_and_remove_biased_features(linked_data, trait)
    note = "Gene expression data for pulmonary arterial hypertension study with Hypertension trait information."

# 6. Validate and save cohort information
is_usable = validate_and_save_cohort_info(
    is_final=True, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=True, 
    is_trait_available=True, 
    is_biased=is_biased,
    df=linked_data,
    note=note
)

# 7. Save the linked data if it's usable
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    linked_data.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Dataset is not usable for trait-gene association studies due to quality issues.")

Normalized gene data saved to ../../output/preprocess/Hypertension/gene_data/GSE117261.csv
Clinical data saved to ../../output/preprocess/Hypertension/clinical_data/GSE117261.csv
Shape of linked data before missing value handling: (84, 24231)
Shape of linked data after missing value handling: (0, 1)
Abnormality detected in the cohort: GSE117261. Preprocessing failed.
A new JSON file was created at: ../../output/preprocess/Hypertension/cohort_info.json
Dataset is not usable for trait-gene association studies due to quality issues.
